## Reference Videos

In [1]:
# https://www.youtube.com/watch?v=o-pZk5R0TZg

## Imports

In [9]:
#  sentence_transformers import SentenceTransformer, InputExample, losses
from torch.utils.data import DataLoader
from sklearn.metrics import classification_report
from sklearn.metrics.pairwise import cosine_similarity
import pandas as pd
import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer
import logging
logging.basicConfig(format='%(asctime)s - %(message)s', level=logging.INFO)

## Import the data, as well as split into a smaller/larger dataset 

In [10]:
# Load datasets
df_examples = pd.read_parquet('shopping_queries_dataset_examples.parquet')
df_products = pd.read_parquet('shopping_queries_dataset_products.parquet')
df_sources = pd.read_csv('shopping_queries_dataset_sources.csv')

In [11]:
# Merge examples with products
df_examples_products = pd.merge(
    df_examples,
    df_products,
    how='left',
    left_on=['product_locale', 'product_id'],
    right_on=['product_locale', 'product_id']
)

# Task 1: Small version (filtered to U.S. locale and non-null titles)
df_task_1 = df_examples_products[
    (df_examples_products["small_version"] == 1) &
    (df_examples_products["product_locale"] == "us") &
    (df_examples_products["product_title"].notnull())
]

# Task 2: Large version
df_task_2 = df_examples_products[df_examples_products["large_version"] == 1]
df_task_2_train = df_task_2[df_task_2["split"] == "train"]
df_task_2_test = df_task_2[df_task_2["split"] == "test"]


## Initial Model: Smaller sample set, only looking at exact matches and using product titles
Scores: REALLY BAD

In [14]:
# Filter to Task 1 Train Set with Relevant (E) Labels
df_task_1_copy = df_task_1[
    (df_task_1["split"] == "train") &
    (df_task_1["esci_label"] == "E")
]

# Sample smaller set if needed (optional)
sample_df = df_task_1_copy.copy()

# Extract queries and product titles
queries = sample_df['query'].astype(str).values
products = sample_df['product_title'].astype(str).values

# TF-IDF Vectorizer on combined
vectorizer = TfidfVectorizer()
query_vecs = vectorizer.fit_transform(queries)
product_vecs = vectorizer.transform(products)  # Use same vocab

# Score and Recommend Top 3 Products per Query
for i, query in enumerate(queries):
    scores = cosine_similarity(query_vecs[i], product_vecs).flatten()
    ranked_indices = scores.argsort()[::-1]
    
    print(f"\nTop matches for: '{query}'")
    for idx in ranked_indices[:3]:
        print(f"- {products[idx]} (score: {scores[idx]:.4f})")


Top matches for: '!awnmower tires without rims'
- 17x7 Enkei EKM3 (Gunmetal) Wheels/Rims 5x100 (442-770-8045GM) (score: 0.4192)
- TDPRO 4PCS 145/70-6 Tires With 6 inch Wheels Rims for ATV Go Kart (score: 0.3681)
- Enkei 17x7 EDR9 (Matte Black) Wheels/Rims 5x100/114.3 (441-770-0245BK) (score: 0.3153)

Top matches for: '!awnmower tires without rims'
- 17x7 Enkei EKM3 (Gunmetal) Wheels/Rims 5x100 (442-770-8045GM) (score: 0.4192)
- TDPRO 4PCS 145/70-6 Tires With 6 inch Wheels Rims for ATV Go Kart (score: 0.3681)
- Enkei 17x7 EDR9 (Matte Black) Wheels/Rims 5x100/114.3 (441-770-0245BK) (score: 0.3153)

Top matches for: '!awnmower tires without rims'
- 17x7 Enkei EKM3 (Gunmetal) Wheels/Rims 5x100 (442-770-8045GM) (score: 0.4192)
- TDPRO 4PCS 145/70-6 Tires With 6 inch Wheels Rims for ATV Go Kart (score: 0.3681)
- Enkei 17x7 EDR9 (Matte Black) Wheels/Rims 5x100/114.3 (441-770-0245BK) (score: 0.3153)

Top matches for: '!awnmower tires without rims'
- 17x7 Enkei EKM3 (Gunmetal) Wheels/Rims 5x10


Top matches for: '# 10 self-seal envelopes without window'
- Self Seal Double Window Security Envelopes (#10 - Box of 500), for Invoices, Statements and Legal Documents (4 1/8" x 9 1/2") (score: 0.6234)
- Office Deed 500 #10 Self Seal Double Window Security Envelopes-Designed for Business Statements, Quickbooks Invoices, and Return Envelopes 4 1/8 X 9 ½’’ (score: 0.6204)
- Office Deed 500 #10 Self Seal Double Window Security Envelopes-Designed for Business Statements, Quickbooks Invoices, and Return Envelopes 4 1/8 X 9 ½’’ (score: 0.6204)

Top matches for: '# 10 self-seal envelopes without window'
- Self Seal Double Window Security Envelopes (#10 - Box of 500), for Invoices, Statements and Legal Documents (4 1/8" x 9 1/2") (score: 0.6234)
- Office Deed 500 #10 Self Seal Double Window Security Envelopes-Designed for Business Statements, Quickbooks Invoices, and Return Envelopes 4 1/8 X 9 ½’’ (score: 0.6204)
- Office Deed 500 #10 Self Seal Double Window Security Envelopes-Designed for B


Top matches for: '# mom life'
- Diliflyer Women's Mom Life Boys Girls Letters T Shirts Graphic Tees (XL, B-mom Life) (score: 0.7344)
- Womens Mom Shirts Mom Life Messy Bun Coffee Run Gangsta Rap Nap T-Shirt (score: 0.6677)
- Mom's Marijuana: Life, Love, and Beating the Odds (score: 0.6203)

Top matches for: '# mom life'
- Diliflyer Women's Mom Life Boys Girls Letters T Shirts Graphic Tees (XL, B-mom Life) (score: 0.7344)
- Womens Mom Shirts Mom Life Messy Bun Coffee Run Gangsta Rap Nap T-Shirt (score: 0.6677)
- Mom's Marijuana: Life, Love, and Beating the Odds (score: 0.6203)

Top matches for: '# mom life'
- Diliflyer Women's Mom Life Boys Girls Letters T Shirts Graphic Tees (XL, B-mom Life) (score: 0.7344)
- Womens Mom Shirts Mom Life Messy Bun Coffee Run Gangsta Rap Nap T-Shirt (score: 0.6677)
- Mom's Marijuana: Life, Love, and Beating the Odds (score: 0.6203)

Top matches for: '#1 best and not expensive bath back brush cream color'
- LFJ 3 in 1 Back Bath Brush Set for Shower, 19" L


Top matches for: '#1 small corded treadmill without remote control'
- Skytech 1001-A remote control (score: 0.5533)
- UREVO 2 in 1 Under Desk Treadmill, 2.5HP Folding Electric Treadmill Walking Jogging Machine for Home Office with Remote Control (score: 0.4822)
- Goplus 2 in 1 Folding Treadmill, 2.25HP Superfit Under Desk Electric Treadmill, Installation-Free with Blue Tooth Speaker, Remote Control, APP Control and LED Display, Walking Jogging for Home Office (score: 0.4470)

Top matches for: '#1 small corded treadmill without remote control'
- Skytech 1001-A remote control (score: 0.5533)
- UREVO 2 in 1 Under Desk Treadmill, 2.5HP Folding Electric Treadmill Walking Jogging Machine for Home Office with Remote Control (score: 0.4822)
- Goplus 2 in 1 Folding Treadmill, 2.25HP Superfit Under Desk Electric Treadmill, Installation-Free with Blue Tooth Speaker, Remote Control, APP Control and LED Display, Walking Jogging for Home Office (score: 0.4470)

Top matches for: '#1 small corded tre


Top matches for: '#10 window envelopes not self seal'
- Self Seal Double Window Security Envelopes (#10 - Box of 500), for Invoices, Statements and Legal Documents (4 1/8" x 9 1/2") (score: 0.6113)
- Office Deed 500 #10 Self Seal Double Window Security Envelopes-Designed for Business Statements, Quickbooks Invoices, and Return Envelopes 4 1/8 X 9 ½’’ (score: 0.6084)
- Office Deed 500 #10 Self Seal Double Window Security Envelopes-Designed for Business Statements, Quickbooks Invoices, and Return Envelopes 4 1/8 X 9 ½’’ (score: 0.6084)

Top matches for: '#10 window envelopes not self seal'
- Self Seal Double Window Security Envelopes (#10 - Box of 500), for Invoices, Statements and Legal Documents (4 1/8" x 9 1/2") (score: 0.6113)
- Office Deed 500 #10 Self Seal Double Window Security Envelopes-Designed for Business Statements, Quickbooks Invoices, and Return Envelopes 4 1/8 X 9 ½’’ (score: 0.6084)
- Office Deed 500 #10 Self Seal Double Window Security Envelopes-Designed for Business St

...


Top matches for: '7xl polo shirts for men big and tall'
- KingSize Men's Big & Tall Pima Piqué Polo Shirt - Big - 7XL, Steel Multicolored (score: 0.7751)
- KingSize Men's Big & Tall Piqué Polo Shirt - Big - 7XL, True Red Multicolored (score: 0.7252)
- KingSize Men's Big & Tall Longer-Length Piqué Polo Shirt - Tall - 7XL, Black (score: 0.6856)

Top matches for: '7xl polo shirts for men big and tall'
- KingSize Men's Big & Tall Pima Piqué Polo Shirt - Big - 7XL, Steel Multicolored (score: 0.7751)
- KingSize Men's Big & Tall Piqué Polo Shirt - Big - 7XL, True Red Multicolored (score: 0.7252)
- KingSize Men's Big & Tall Longer-Length Piqué Polo Shirt - Tall - 7XL, Black (score: 0.6856)

Top matches for: '7xl polo shirts for men big and tall'
- KingSize Men's Big & Tall Pima Piqué Polo Shirt - Big - 7XL, Steel Multicolored (score: 0.7751)
- KingSize Men's Big & Tall Piqué Polo Shirt - Big - 7XL, True Red Multicolored (score: 0.7252)
- KingSize Men's Big & Tall Longer-Length Piqué Polo Shir


Top matches for: '8 billiard table'
- Classic Sport - 87" Dunhill Billiard Table, Mid-Size Indoor Pool Table with Green Felt Surface, Billiard Cues, Billiard Balls Set, and Accessories, Brown (score: 0.7323)
- Mizerak Donovan II 8' Billiard Table with 2 Cues, Set of Billiard Balls, Triangle Brush and 2 Chalk (score: 0.6668)
- Mizerak Donovan II 8' Billiard Table with 2 Cues, Set of Billiard Balls, Triangle Brush and 2 Chalk (score: 0.6668)

Top matches for: '8 billiard table'
- Classic Sport - 87" Dunhill Billiard Table, Mid-Size Indoor Pool Table with Green Felt Surface, Billiard Cues, Billiard Balls Set, and Accessories, Brown (score: 0.7323)
- Mizerak Donovan II 8' Billiard Table with 2 Cues, Set of Billiard Balls, Triangle Brush and 2 Chalk (score: 0.6668)
- Mizerak Donovan II 8' Billiard Table with 2 Cues, Set of Billiard Balls, Triangle Brush and 2 Chalk (score: 0.6668)

Top matches for: '8 billiard table'
- Classic Sport - 87" Dunhill Billiard Table, Mid-Size Indoor Pool Table 


Top matches for: '8 in pot saucer'
- The HC Companies SLI10000E21C012LRTKG KZART Akro Mils SLI10000E21 Saucer for 10-Inch Classic Pot, Chocolat, Chocolate (score: 0.5720)
- REMIAWY Plant Saucer, 18 Pack of 6 8 10 Inch Plastic Plant Saucers for Indoors Outdoors Clear Flower Pot Drip Trays Plants Garden Saucers Plant Pot Saucer Trays (score: 0.4711)
- Dahlia 5.5'' Inch Rustic Drip Glazed Ceramic Planter/Succulent Pot/Plant Pot w. Saucer/Tray (score: 0.4689)

Top matches for: '8 in pot saucer'
- The HC Companies SLI10000E21C012LRTKG KZART Akro Mils SLI10000E21 Saucer for 10-Inch Classic Pot, Chocolat, Chocolate (score: 0.5720)
- REMIAWY Plant Saucer, 18 Pack of 6 8 10 Inch Plastic Plant Saucers for Indoors Outdoors Clear Flower Pot Drip Trays Plants Garden Saucers Plant Pot Saucer Trays (score: 0.4711)
- Dahlia 5.5'' Inch Rustic Drip Glazed Ceramic Planter/Succulent Pot/Plant Pot w. Saucer/Tray (score: 0.4689)

Top matches for: '8 in pot saucer'
- The HC Companies SLI10000E21C012LRTKG KZ


Top matches for: '8 inch woofer marine'
- Sami 5" MID WOOFER Speaker 8 OHMS @ 20 WATTS (score: 0.4427)
- Marine Metal Bubbles Pump B-3 (score: 0.3762)
- Yarrow Stalks (7 Inch) (score: 0.3672)

Top matches for: '8 inch woofer marine'
- Sami 5" MID WOOFER Speaker 8 OHMS @ 20 WATTS (score: 0.4427)
- Marine Metal Bubbles Pump B-3 (score: 0.3762)
- Yarrow Stalks (7 Inch) (score: 0.3672)

Top matches for: '8 inch woofer marine'
- Sami 5" MID WOOFER Speaker 8 OHMS @ 20 WATTS (score: 0.4427)
- Marine Metal Bubbles Pump B-3 (score: 0.3762)
- Yarrow Stalks (7 Inch) (score: 0.3672)

Top matches for: '8 inch woofer marine'
- Sami 5" MID WOOFER Speaker 8 OHMS @ 20 WATTS (score: 0.4427)
- Marine Metal Bubbles Pump B-3 (score: 0.3762)
- Yarrow Stalks (7 Inch) (score: 0.3672)

Top matches for: '8 inch woofer marine'
- Sami 5" MID WOOFER Speaker 8 OHMS @ 20 WATTS (score: 0.4427)
- Marine Metal Bubbles Pump B-3 (score: 0.3762)
- Yarrow Stalks (7 Inch) (score: 0.3672)

Top matches for: '8 inch woofer ma

KeyboardInterrupt: 

In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity

# Filter to Task 1 Train Set with Relevant (E) Labels
df_task_1_copy = df_task_1[
    (df_task_1["split"] == "train") &
    (df_task_1["esci_label"] == "E")
].copy()

# Fill missing values and combine product metadata (for retrieval)
df_task_1_copy['product_title'] = df_task_1_copy['product_title'].fillna('')
df_task_1_copy['product_description'] = df_task_1_copy['product_description'].fillna('')
df_task_1_copy['product_brand'] = df_task_1_copy['product_brand'].fillna('')
df_task_1_copy['product_bullet_point'] = df_task_1_copy['product_bullet_point'].fillna('')

df_task_1_copy['full_product_text'] = (
    df_task_1_copy['product_title'] + ' ' +
    df_task_1_copy['product_description'] + ' ' +
    df_task_1_copy['product_brand'] + ' ' +
    df_task_1_copy['product_bullet_point']
)

# Extract queries and product titles for display
queries = df_task_1_copy['query'].astype(str).tolist()
product_texts = df_task_1_copy['full_product_text'].astype(str).tolist()
product_titles = df_task_1_copy['product_title'].astype(str).tolist()

# TF-IDF Vectorizer on combined corpus
vectorizer = TfidfVectorizer()
query_vecs = vectorizer.fit_transform(queries)
product_vecs = vectorizer.transform(product_texts)

# Score and Recommend Top 3 Product Titles per Query
for i, query in enumerate(queries):
    scores = cosine_similarity(query_vecs[i], product_vecs).flatten()
    ranked_indices = scores.argsort()[::-1]
    
    print(f"\nTop matches for: '{query}'")
    for idx in ranked_indices[:3]:
        print(f"- {product_titles[idx]} (score: {scores[idx]:.4f})")


## Incorporate Sentence Transformers (this library literally not working for me and I've been trying to fix for two hours lol. Going to leave this in as a model that would've been great if it worked)

In [ ]:
import pandas as pd
import numpy as np
from sentence_transformers import SentenceTransformer
from sklearn.metrics.pairwise import cosine_similarity

# Sample 20 rows from Task 1 (you can adjust this as needed)
sample_df = df_task_1.sample(n=20, random_state=42).copy()

# Ensure bullet point and other fields exist
sample_df['product_bullet_point'] = sample_df.get('product_bullet_point', '').fillna('')
sample_df['product_description'] = sample_df['product_description'].fillna('')
sample_df['product_brand'] = sample_df['product_brand'].fillna('')
sample_df['product_title'] = sample_df['product_title'].fillna('')

# Combine metadata into a single product string
sample_df['full_product_text'] = (
    sample_df['product_title'] + ' ' +
    sample_df['product_description'] + ' ' +
    sample_df['product_brand'] + ' ' +
    sample_df['product_bullet_point']
)

# Prepare text for encoding
queries = sample_df['query'].astype(str).tolist()
products = sample_df['full_product_text'].astype(str).tolist()

# Load sentence-transformer model
model = SentenceTransformer('all-MiniLM-L6-v2')

# Compute embeddings
query_vecs = model.encode(queries, convert_to_numpy=True)
product_vecs = model.encode(products, convert_to_numpy=True)

# Compute similarity and print top matches
for i, query in enumerate(queries):
    scores = cosine_similarity(query_vecs[i].reshape(1, -1), product_vecs).flatten()
    
    # Normalize scores
    scores = (scores - scores.min()) / (scores.max() - scores.min() + 1e-8)
    ranked_indices = scores.argsort()[::-1]
    
    print(f"\nTop matches for: '{query}'")
    for idx in ranked_indices[:3]:
        title = sample_df.iloc[idx]['product_title']
        print(f"- {title} (score: {scores[idx]:.4f})")


## Incorporate training and test

In [ ]:
import pandas as pd
import numpy as np
from sentence_transformers import SentenceTransformer
from sklearn.metrics.pairwise import cosine_similarity

# Sample train data and construct product text
train_df = df_task_1_train.sample(n=30, random_state=42).copy()
train_df['product_title'] = train_df['product_title'].fillna('')
train_df['product_description'] = train_df['product_description'].fillna('')
train_df['product_brand'] = train_df['product_brand'].fillna('')
train_df['product_bullet_point'] = train_df.get('product_bullet_point', '').fillna('')

train_df['full_product_text'] = (
    train_df['product_title'] + ' ' +
    train_df['product_description'] + ' ' +
    train_df['product_brand'] + ' ' +
    train_df['product_bullet_point']
)

train_products = train_df['full_product_text'].astype(str).tolist()
train_titles = train_df['product_title'].astype(str).tolist()  # for display

# Prepare test queries
test_df = df_task_1_test.sample(n=5, random_state=24).copy()
test_queries = test_df['query'].astype(str).tolist()

# Load the model and compute embeddings
model = SentenceTransformer('all-MiniLM-L6-v2')
product_vecs = model.encode(train_products, convert_to_numpy=True)
query_vecs = model.encode(test_queries, convert_to_numpy=True)

# Recommend top-3 products for each test query
for i, query in enumerate(test_queries):
    scores = cosine_similarity(query_vecs[i].reshape(1, -1), product_vecs).flatten()
    
    # Normalize scores between 0 and 1
    scores = (scores - scores.min()) / (scores.max() - scores.min() + 1e-8)
    ranked_indices = scores.argsort()[::-1]

    print(f"\nTop matches for test query: '{query}'")
    for idx in ranked_indices[:3]:
        print(f"- {train_titles[idx]} (score: {scores[idx]:.4f})")


## Trying to use Recall and MRR (This doesn't work)

In [ ]:
# === Filter for US, Exact Matches, Titles Present ===
df_task_1 = df[
    (df["small_version"] == 1) &
    (df["product_locale"] == "us") &
    (df["product_title"].notnull()) &
    (df["esci_label"] == "E")
]

# === Full Train and Test Sets ===
df_train = df_task_1[df_task_1["split"] == "train"].copy()
df_test = df_task_1[df_task_1["split"] == "test"].sample(n=20, random_state=24).copy()

# === Build full product metadata ===
df_train['full_product_text'] = (
    df_train['product_title'].fillna('') + ' ' +
    df_train['product_description'].fillna('') + ' ' +
    df_train['product_brand'].fillna('')
)

# === SentenceTransformer Embeddings ===
model = SentenceTransformer('all-MiniLM-L6-v2')
product_vecs = model.encode(df_train['full_product_text'].values, convert_to_tensor=True)
product_ids = df_train['product_id'].values

query_vecs = model.encode(df_test['query'].values, convert_to_tensor=True)
true_ids = df_test['product_id'].values

# === Evaluate Recall@3 and MRR@3 ===
k = 3
recall_hits = 0
reciprocal_ranks = []

for i in range(len(df_test)):
    scores = cosine_similarity(
        query_vecs[i].cpu().numpy().reshape(1, -1),
        product_vecs.cpu().numpy()
    ).flatten()

    ranked_indices = scores.argsort()[::-1][:k]
    retrieved_ids = product_ids[ranked_indices]

    print(f"\n🔍 Query: {df_test.iloc[i]['query']}")
    print("Top retrieved product IDs:", list(retrieved_ids))
    print("True product ID:", true_ids[i])

    if true_ids[i] in retrieved_ids:
        recall_hits += 1
        rank = list(retrieved_ids).index(true_ids[i]) + 1
        reciprocal_ranks.append(1.0 / rank)
    else:
        reciprocal_ranks.append(0.0)

recall_at_k = recall_hits / len(df_test)
mrr_at_k = np.mean(reciprocal_ranks)

print(f"\n✨ Evaluation Results (Full Train Set):")
print(f"Recall@{k}: {recall_at_k:.4f}")
print(f"MRR@{k}:    {mrr_at_k:.4f}")